# Test of Altair interactive graphs

### Graphs by country

In [55]:
#hide_input
import ipywidgets as widgets
import altair as alt
from IPython.display import display
from ipywidgets import interact
import pandas as pd

sigma = 0.01
rho = 0.01
tab_name = 'Param_pcm1_esig_{:3.2f}_erho_{:3.2f}'.format(sigma,rho)



data = pd.read_excel("C:\\Users\\julie\\Documents\\GitHub\\test-blog\\input_data\\results_baseline.xlsx",sheet_name=tab_name)
mapping_industry = pd.read_csv("C:\\Users\\julie\\Documents\\GitHub\\test-blog\\input_data\\Indcode.csv")

old_columns = data.columns.values.tolist()
new_columns = ['years','country','Indcode','beta', 'alpha']
new_columns = new_columns + mapping_industry.Name.values.tolist()
new_columns = new_columns + ['s', 'markups', 'markups_supplier', 'xshare']

columns_dict = {old_columns[i]: new_columns[i] for i in range(len(old_columns))}

data_renamed = data.rename(columns=columns_dict)
data_renamed = data_renamed.merge(mapping_industry, on='Indcode', how='left')
data_renamed = data_renamed.drop(columns = ['Indcode','years'])


data_markups = data_renamed.drop(columns=mapping_industry.Name.values.tolist()+['beta', 'alpha', 's', 'xshare'])
data_indicators = data_renamed.drop(columns=mapping_industry.Name.values.tolist()+['markups_supplier','markups'])
data_flows = data_renamed.drop(columns=['beta', 'alpha', 's', 'markups', 'markups_supplier', 'xshare'])

data_indicators = data_indicators.melt(['country','Name'], var_name='indicators', value_name='value')
data_flows = data_flows.melt(['country','Name'], var_name='suppliers', value_name='value')



In [64]:
#hide_input
alt.data_transformers.disable_max_rows()


# Define the 3 Charts
chart_1 = alt.Chart(data_indicators, width=300, height=300).mark_bar(opacity=.50).transform_filter(
    alt.FieldOneOfPredicate(
        field='indicators', oneOf=['s','beta'])).encode(
    x='Name:N',
    y=alt.Y('value:Q',stack=None),
    color=alt.Color('indicators', scale=alt.Scale(domain=['beta','s'], range=['red','blue'])))

chart_2 = alt.Chart(data_markups, width=300, height=300).mark_point().encode(
    x='markups:Q',
    y='markups_supplier:Q',
    tooltip=['Name', 'country', 'markups', 'markups_supplier'])

chart_3 = alt.Chart(data_flows,width = 600, height = 600).mark_rect().encode(
    x='suppliers:N',
    y='Name:N',
    color = 'value:Q',
    tooltip=['value'])


# Define the Country Dropdown
country_dropdown = alt.binding_select(options=data_renamed.country.unique())
country_select = alt.selection_single(fields=['country'], bind=country_dropdown, name='Select')


# Define interactive charts
filter_chart_1 = chart_1.add_selection(
    country_select
).transform_filter(
    country_select
).properties(title="Impact of each Sector by country")

filter_chart_2 = chart_2.add_selection(
    country_select
).transform_filter(
    country_select
).properties(title="Markups by country")

filter_chart_3 = chart_3.add_selection(
    country_select
).transform_filter(
    country_select
).properties(title="I/O parameters by country")


# Display charts
(filter_chart_1 | filter_chart_2) & (filter_chart_3)

alt.VConcatChart(...)

In [38]:
data_flows

country                                               Name  \
0         AUS         Agriculture, Hunting, Forestry and Fishing   
1         AUS                               Mining and Quarrying   
2         AUS                        Food, Beverages and Tobacco   
3         AUS                      Textiles and Textile Products   
4         AUS                      Leather, Leather and Footwear   
...       ...                                                ...   
33295     USA  Other Supporting and Auxiliary Transport Activ...   
33296     USA                        Post and Telecommunications   
33297     USA                           Financial Intermediation   
33298     USA                             Real Estate Activities   
33299     USA      Renting of M&Eq and Other Business Activities   

                                           suppliers     value  
0         Agriculture, Hunting, Forestry and Fishing  0.252750  
1         Agriculture, Hunting, Forestry and Fishing  0.001230  
2         Agriculture, Hunting, Forestry and Fishing  0.337064  
3         Agriculture, Hunting, Forestry and Fishing  0.175253  
4         Agriculture, Hunting, Forestry and Fishing  0.150525  
...                                              ...       ...  
33295  Renting of M&Eq and Other Business Activities  0.242712  
33296  Renting of M&Eq and Other Business Activities  0.276128  
33297  Renting of M&Eq and Other Business Activities  0.261084  
33298  Renting of M&Eq and Other Business Activities  0.171947  
33299  Renting of M&Eq and Other Business Activities  0.414322  

[33300 rows x 4 columns]

In [39]:
data_indicators

country                                               Name indicators  \
0        AUS         Agriculture, Hunting, Forestry and Fishing       beta   
1        AUS                               Mining and Quarrying       beta   
2        AUS                        Food, Beverages and Tobacco       beta   
3        AUS                      Textiles and Textile Products       beta   
4        AUS                      Leather, Leather and Footwear       beta   
...      ...                                                ...        ...   
6655     USA  Other Supporting and Auxiliary Transport Activ...     xshare   
6656     USA                        Post and Telecommunications     xshare   
6657     USA                           Financial Intermediation     xshare   
6658     USA                             Real Estate Activities     xshare   
6659     USA      Renting of M&Eq and Other Business Activities     xshare   

         value  
0     0.037056  
1     0.056010  
2     0.071822  
3     0.009246  
4     0.001927  
...        ...  
6655  0.295707  
6656  0.361224  
6657  0.416224  
6658  0.252908  
6659  0.320387  

[6660 rows x 4 columns]